## Deliverable 3

In [1]:
# Import our dependencies
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,OneHotEncoder
import pandas as pd
import tensorflow as tf

# 1-2.Import and read the charity_data.csv.
import pandas as pd 
application_df = pd.read_csv("Resources/charity_data.csv")
application_df.head()

EIN                                      NAME APPLICATION_TYPE  \
0  10520599              BLUE KNIGHTS MOTORCYCLE CLUB              T10   
1  10531628    AMERICAN CHESAPEAKE CLUB CHARITABLE TR               T3   
2  10547893        ST CLOUD PROFESSIONAL FIREFIGHTERS               T5   
3  10553066            SOUTHSIDE ATHLETIC ASSOCIATION               T3   
4  10556103  GENETIC RESEARCH INSTITUTE OF THE DESERT               T3   

        AFFILIATION CLASSIFICATION      USE_CASE  ORGANIZATION  STATUS  \
0       Independent          C1000    ProductDev   Association       1   
1       Independent          C2000  Preservation  Co-operative       1   
2  CompanySponsored          C3000    ProductDev   Association       1   
3  CompanySponsored          C2000  Preservation         Trust       1   
4       Independent          C1000     Heathcare         Trust       1   

      INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  IS_SUCCESSFUL  
0              0                      N     5000              1  
1         1-9999                      N   108590              1  
2              0                      N     5000              0  
3    10000-24999                      N     6692              1  
4  100000-499999                      N   142590              1

In [2]:
# 3. Pre-process the dataset
#* Drop the non-beneficial ID columns, 'EIN' and 'NAME'.
application_df = application_df.drop(['EIN','NAME'], axis=1)
#* Determine the number of unique values in each column.
application_df.nunique()
#* Look at APPLICATION_TYPE value counts for binning
appType = application_df['APPLICATION_TYPE'].value_counts()
#* Determine which values to replace if counts are less than ...?
replace_application = appType.index
# Replace in dataframe
for app in replace_application:
    if appType[app] < 500:
        application_df.APPLICATION_TYPE = application_df.APPLICATION_TYPE.replace(app,"Other")
    
#* Look at CLASSIFICATION value counts for binning
classification = application_df['CLASSIFICATION'].value_counts()
#* Determine which values to replace if counts are less than ..?
replace_class = classification.index
# Replace in dataframe
for cls in replace_class:
    if classification[cls] < 1800:
        application_df.CLASSIFICATION = application_df.CLASSIFICATION.replace(cls,"Other")        

In [3]:
# 3** Adding modifications in Pre-processing to optimize the model...
# get rid off two columns that I think do not have major impact in the classification problem
application_df = application_df.drop(['ASK_AMT','SPECIAL_CONSIDERATIONS'], axis=1)

In [4]:
#* Generate categorical variable lists
application_cat = application_df.dtypes[application_df.dtypes == "object"].index.tolist()

#* Create a OneHotEncoder instance for encoding all categorical variable list at once
enc = OneHotEncoder(sparse=False)

#* Fit and transform the OneHotEncoder using the categorical variable list
encode_df = pd.DataFrame(enc.fit_transform(application_df[application_cat]))

#* Add the encoded variable names to the dataframe
encode_df.columns = enc.get_feature_names(application_cat)
encode_df.head()

APPLICATION_TYPE_Other  APPLICATION_TYPE_T10  APPLICATION_TYPE_T19  \
0                     0.0                   1.0                   0.0   
1                     0.0                   0.0                   0.0   
2                     0.0                   0.0                   0.0   
3                     0.0                   0.0                   0.0   
4                     0.0                   0.0                   0.0   

   APPLICATION_TYPE_T3  APPLICATION_TYPE_T4  APPLICATION_TYPE_T5  \
0                  0.0                  0.0                  0.0   
1                  1.0                  0.0                  0.0   
2                  0.0                  0.0                  1.0   
3                  1.0                  0.0                  0.0   
4                  1.0                  0.0                  0.0   

   APPLICATION_TYPE_T6  APPLICATION_TYPE_T7  APPLICATION_TYPE_T8  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   AFFILIATION_CompanySponsored  ...  ORGANIZATION_Trust  INCOME_AMT_0  \
0                           0.0  ...                 0.0           1.0   
1                           0.0  ...                 0.0           0.0   
2                           1.0  ...                 0.0           1.0   
3                           1.0  ...                 1.0           0.0   
4                           0.0  ...                 1.0           0.0   

   INCOME_AMT_1-9999  INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  \
0                0.0                     0.0                       0.0   
1                1.0                     0.0                       0.0   
2                0.0                     0.0                       0.0   
3                0.0                     1.0                       0.0   
4                0.0                     0.0                       1.0   

   INCOME_AMT_10M-50M  INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  \
0                 0.0               0.0                     0.0   
1                 0.0               0.0                     0.0   
2                 0.0               0.0                     0.0   
3                 0.0               0.0                     0.0   
4                 0.0               0.0                     0.0   

   INCOME_AMT_50M+  INCOME_AMT_5M-10M  
0              0.0                0.0  
1              0.0                0.0  
2              0.0                0.0  
3              0.0                0.0  
4              0.0                0.0  

[5 rows x 39 columns]

In [5]:
#* Merge one-hot encoded features and drop the originals
application_df = application_df.merge(encode_df,left_index=True, right_index=True)
application_df = application_df.drop(application_cat, axis=1)
application_df.head()

STATUS  IS_SUCCESSFUL  APPLICATION_TYPE_Other  APPLICATION_TYPE_T10  \
0       1              1                     0.0                   1.0   
1       1              1                     0.0                   0.0   
2       1              0                     0.0                   0.0   
3       1              1                     0.0                   0.0   
4       1              1                     0.0                   0.0   

   APPLICATION_TYPE_T19  APPLICATION_TYPE_T3  APPLICATION_TYPE_T4  \
0                   0.0                  0.0                  0.0   
1                   0.0                  1.0                  0.0   
2                   0.0                  0.0                  0.0   
3                   0.0                  1.0                  0.0   
4                   0.0                  1.0                  0.0   

   APPLICATION_TYPE_T5  APPLICATION_TYPE_T6  APPLICATION_TYPE_T7  ...  \
0                  0.0                  0.0                  0.0  ...   
1                  0.0                  0.0                  0.0  ...   
2                  1.0                  0.0                  0.0  ...   
3                  0.0                  0.0                  0.0  ...   
4                  0.0                  0.0                  0.0  ...   

   ORGANIZATION_Trust  INCOME_AMT_0  INCOME_AMT_1-9999  \
0                 0.0           1.0                0.0   
1                 0.0           0.0                1.0   
2                 0.0           1.0                0.0   
3                 1.0           0.0                0.0   
4                 1.0           0.0                0.0   

   INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  INCOME_AMT_10M-50M  \
0                     0.0                       0.0                 0.0   
1                     0.0                       0.0                 0.0   
2                     0.0                       0.0                 0.0   
3                     1.0                       0.0                 0.0   
4                     0.0                       1.0                 0.0   

   INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  INCOME_AMT_50M+  \
0               0.0                     0.0              0.0   
1               0.0                     0.0              0.0   
2               0.0                     0.0              0.0   
3               0.0                     0.0              0.0   
4               0.0                     0.0              0.0   

   INCOME_AMT_5M-10M  
0                0.0  
1                0.0  
2                0.0  
3                0.0  
4                0.0  

[5 rows x 41 columns]

In [6]:
#* Split our preprocessed data into our features and target arrays
y = (application_df["IS_SUCCESSFUL"]==1).values
X = application_df.drop(["IS_SUCCESSFUL"],axis = 1).values

#* Split the preprocessed data into a training and testing dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=78)

#* Standardize using StandardScaler, then scale the data.
scaler = StandardScaler()
X_scaler = scaler.fit(X_train)
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [7]:
#4.Define the model - deep neural net, i.e., the number of input features and hidden nodes for each layer.
number_input_features = len(X_train[0])
hidden_nodes_layer1 = 20
hidden_nodes_layer2 = 10
hidden_nodes_layer3 = 5
nn = tf.keras.models.Sequential()

#First hidden layer
nn.add(
    tf.keras.layers.Dense(units = hidden_nodes_layer1, input_dim = number_input_features, activation = "relu")
)
#Second hidden layer
nn.add(
    tf.keras.layers.Dense(units = hidden_nodes_layer2, activation = "relu")
)
#Third hidden layer
nn.add(
    tf.keras.layers.Dense(units = hidden_nodes_layer3, activation = "relu")
)
#Output layer
nn.add(
    tf.keras.layers.Dense(units = 1, activation = "sigmoid")
)
#Check the structure of the model
nn.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 20)                820       
_________________________________________________________________
dense_1 (Dense)              (None, 10)                210       
_________________________________________________________________
dense_2 (Dense)              (None, 5)                 55        
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 6         
Total params: 1,091
Trainable params: 1,091
Non-trainable params: 0
_________________________________________________________________


2021-12-17 15:40:33.390417: I tensorflow/core/platform/cpu_feature_guard.cc:145] This TensorFlow binary is optimized with Intel(R) MKL-DNN to use the following CPU instructions in performance critical operations:  SSE4.1 SSE4.2
To enable them in non-MKL-DNN operations, rebuild TensorFlow with the appropriate compiler flags.
2021-12-17 15:40:33.391261: I tensorflow/core/common_runtime/process_util.cc:115] Creating new thread pool with default inter op setting: 8. Tune using inter_op_parallelism_threads for best performance.


In [8]:
#5. Callback and save the model every 5 epochs
# Import checkpoint dependencies
import os
from tensorflow.keras.callbacks import ModelCheckpoint

# Define the checkpoint path and filenames
os.makedirs("checkpoints_Opt3/",exist_ok = True)
checkpoint_path = "checkpoints_Opt3/weights.{epoch:02d}.hdf5"
cp_callback = ModelCheckpoint(
    filepath = checkpoint_path,
    verbose = 1,
    save_weights_only = True,
    save_freq = 5)

In [9]:
#6.Compile the model
nn.compile(loss = "binary_crossentropy", optimizer = "adam", metrics = ["accuracy"])
# Train the model
fit_model = nn.fit(X_train_scaled, y_train, epochs = 100, callbacks = [cp_callback])

Train on 25724 samples
Epoch 1/100

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
   32/25724 [..............................] - ETA: 7:44 - loss: 0.7297 - accuracy: 0.3750
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
  224/25724 [..............................] - ETA: 1:11 - loss: 0.7003 - accuracy: 0.5000
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
  256/25724 [..............................] - ETA: 1:08 - loss: 0.6996 - accuracy: 0.5039
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
  288/25724 [..............................] - ETA: 1:11 - loss: 0.7003 - accuracy: 0.5104
Epoch 00001: saving model to checkpoi


Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
 3424/25724 [==>...........................] - ETA: 10s - loss: 0.6776 - accuracy: 0.5549
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
 3648/25724 [===>..........................] - ETA: 9s - loss: 0.6769 - accuracy: 0.5551 
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Ep


Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
 6976/25724 [=======>......................] - ETA: 6s - loss: 0.6596 - accuracy: 0.5956
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
 7200/25724 [=======>......................] - ETA: 6s - loss: 0.6581 - accuracy: 0.5994
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoc


Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
10560/25724 [===========>..................] - ETA: 4s - loss: 0.6388 - accuracy: 0.6373
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
10784/25724 [===========>..................] - ETA: 4s - loss: 0.6373 - accuracy: 0.6400
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoc

14016/25724 [===============>..............] - ETA: 3s - loss: 0.6269 - accuracy: 0.6586
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5
14272/25724 [===============>..............] - ETA: 3s - loss: 0.6259 - accuracy: 0.6597
Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoch 00001: saving model to checkpoints_Opt3/weights.01.hdf5

Epoc

...

15648/25724 [=================>............] - ETA: 10s - loss: 0.5418 - accuracy: 0.7362
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
15744/25724 [=================>............] - ETA: 10s - loss: 0.5417 - accuracy: 0.7363
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
15840/25724 [=================>............] - ETA: 10s - loss: 0.5415 - accuracy: 0.7366
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
15904/25724 [=================>............] - ETA: 10s - loss: 0.5416 - accuracy: 0.7364
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epo

18048/25724 [====================>.........] - ETA: 8s - loss: 0.5417 - accuracy: 0.7356
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
18080/25724 [====================>.........] - ETA: 8s - loss: 0.5419 - accuracy: 0.7356
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
18144/25724 [====================>.........] - ETA: 8s - loss: 0.5423 - accuracy: 0.7352
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
18208/25724 [====================>.........] - ETA: 7s - loss: 0.5419 - accuracy: 0.7356
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
18272/25724 [====================>.........] - ETA: 7s - loss: 0.5417 - accuracy: 0.7358
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
18304/25724 [====================>.........] - E

20384/25724 [======================>.......] - ETA: 5s - loss: 0.5400 - accuracy: 0.7375
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
20512/25724 [======================>.......] - ETA: 5s - loss: 0.5399 - accuracy: 0.7375
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
20608/25724 [=======================>......] - ETA: 5s - loss: 0.5393 - accuracy: 0.7382
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
20704/25724 [=======================>......] - ETA: 5s - loss: 0.5395 - accuracy: 0.7380
Epoch 0

22752/25724 [=========================>....] - ETA: 3s - loss: 0.5393 - accuracy: 0.7382
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
22784/25724 [=========================>....] - ETA: 3s - loss: 0.5393 - accuracy: 0.7382
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
22816/25724 [=========================>....] - ETA: 3s - loss: 0.5392 - accuracy: 0.7384
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
22848/25724 [=========================>....] - ETA: 3s - loss: 0.5390 - accuracy: 0.7384
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
22976/25724 [=========================>....] - ETA: 3s - loss: 0.5390 - accuracy: 0.7384
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/w

24992/25724 [============================>.] - ETA: 0s - loss: 0.5400 - accuracy: 0.7385
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25024/25724 [============================>.] - ETA: 0s - loss: 0.5400 - accuracy: 0.7383
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25056/25724 [============================>.] - ETA: 0s - loss: 0.5399 - accuracy: 0.7384
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25088/25724 [============================>.] - ETA: 0s - loss: 0.5398 - accuracy: 0.7384
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25120/25724 [============================>.] - ETA: 0s - loss: 0.5398 - accuracy: 0.7385
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5

Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25184/25724 [============================>.] - ETA: 0s - loss: 0.5398 - accuracy: 0.7386
Epoch 00100: saving model to checkpoints_Opt3/weights.100.hdf5
25216/25724 [===========

In [ ]:
#7.Evaluate the model using the test data
model_loss, model_accuracy = nn.evaluate(X_test_scaled, y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")